In [3]:
# Importing relevant libraries
import pandas as pd
import numpy as np
import json

In [20]:
# Fixing and cleaning up the new categories mapping
with open(r"./dataset/categories.txt")as f:
    CATEGORIES = json.load(f)

CATEGORIES = set(CATEGORIES.keys())

IGNORED_CATEGOREIES = set([
  "atom-ph", "bayes-an", "chao-dyn", "chem-ph", "cmp-lg", "comp-gas", "cond-mat", "dg-ga", "funct-an",
  "mtrl-th", "patt-sol", "plasm-ph", "q-alg", "q-bio", "solv-int", "supr-con", "test", "test.dis-nn", 
  "test.mes-hall", "test.mtrl-sci", "test.soft", "test.stat-mech", "test.str-el", "test.supr-con"
])

CATEGORY_ALIASES = {
  'math.MP': 'math-ph',
  'stat.TH': 'math.ST',
  'math.IT': 'cs.IT',
  'q-fin.EC': 'econ.GN',
  'cs.SY': 'eess.SY',
  'cs.NA': 'math.NA'
}

In [ ]:
for I_CAT in IGNORED_CATEGOREIES:
    if I_CAT in CATEGORIES:
        CATEGORIES.remove(I_CAT)

for C_ALIAS in CATEGORY_ALIASES:
    if C_ALIAS in CATEGORIES:
        CATEGORIES.remove(C_ALIAS)
        CATEGORIES.add(CATEGORY_ALIASES[C_ALIAS])

CATEGORIES = sorted(list(CATEGORIES))
CATEGORIES = {CATEGORIES[i]:i for i in range(len(CATEGORIES))}
with open(r"./dataset/categories.txt", "w")as f:
    json.dump(CATEGORIES, f)

#### For now only keep version 1

In [5]:
# Cleaning the dataset, ie. removing duplicates, verifying none of the ignored tags are there and replace category aliases
test_minor_path = r"dataset/full_text_sample/test_minor_cats_full.json"
train_minor_path = r"dataset/full_text_sample/train_minor_cats_full.json"

In [41]:
# Fixing test
pd_test_minor = pd.read_json(test_minor_path, lines=True)

pd_test_minor.rename(columns={'major_category':'field','prime_category':'primary_subfield','abs_categories':'secondary_subfield'}, inplace=True)
pd_test_minor = pd_test_minor[~pd_test_minor['field'].isin(IGNORED_CATEGOREIES)]
pd_test_minor = pd_test_minor[(pd_test_minor['version'] == 1)]
if pd_test_minor['primary_subfield'].isin(CATEGORY_ALIASES.keys()).sum():
    ValueError("IMPLEMENT CODE TO CHANGE CATEGORY_ALIASES")
        
pd_test_minor[['primary_subfield', "secondary_subfield"]].to_csv("dataset/baseline_datasets/test_field.csv")
test_fields["Usage"] = "Public"
pd_test_minor.drop(columns=['field', 'primary_subfield', "secondary_subfield"]).to_csv(r"dataset/baseline_datasets/test_papers.csv")

In [43]:
# Fixing train
chunksize = 10**4
for i, pd_train_minor in enumerate(pd.read_json(train_minor_path, lines=True, chunksize=chunksize)):
    print(f"Chunk {i+1}")
    pd_train_minor.rename(columns={'major_category':'field','prime_category':'primary_subfield','abs_categories':'secondary_subfield'}, inplace=True)
    pd_train_minor = pd_train_minor[~pd_train_minor['field'].isin(IGNORED_CATEGOREIES)]
    pd_train_minor = pd_train_minor[(pd_train_minor['version'] == 1)]
    if pd_train_minor['primary_subfield'].isin(CATEGORY_ALIASES.keys()).sum():
        ValueError("IMPLEMENT CODE TO CHANGE CATEGORY_ALIASES ")

    if i==0:
        pd_train_minor.to_csv(r"dataset/baseline_datasets/train.csv")
    else:
        pd_train_minor.to_csv(r"dataset/baseline_datasets/train.csv", header=False, mode='a')

Chunk 1
Chunk 2
Chunk 3
Chunk 4
Chunk 5
Chunk 6
Chunk 7
Chunk 8
Chunk 9
Chunk 10
Chunk 11
Chunk 12


#### Removing using titles

In [123]:
# TBD whether we do this or not
duplicates = pd_test_minor[pd_test_minor.duplicated(subset=['title'], keep=False)]
duplicates

paper_id  version  yymm              created  \
3888  1006.1164        2  1006  2010-06-10T05:56:49   
3957  1011.0157        1  1011  2010-10-31T14:09:45   

                                                  title secondary_subfield  \
3888  Non-perturbative renormalization of quark mass...            hep-lat   
3957  Non-perturbative renormalization of quark mass...            hep-lat   

                                               abstract primary_subfield  \
3888  We present an evaluation of the quark mass ren...          hep-lat   
3957  We present an evaluation of the quark mass ren...          hep-lat   

        field                                           fulltext  
3888  hep-lat  UTHEP-609\nUTCCS-P-59\n\nNon-perturbative reno...  
3957  hep-lat  Non-perturbative renormalization of quark mass...

#### Score metrics used on Kaggle

In [66]:
def score(solution: pd.DataFrame, submission: pd.DataFrame, row_id_column_name: str) -> float:

    try:
        # First calculate the primary subfield accuracy which is relatively simple
        res = solution["primary_subfield"]==submission["primary_subfield"]
        primary_field_acc = res.sum()/len(res)

        # We then calculate the secondary field accuracy
        sol_sec_list = solution["secondary_subfield"].tolist()
        sub_sec_list = solution["secondary_subfield"].tolist()

        secondary_field_acc = 0
        for i in range(len(sol_sec_list)):
            paper_secondary_field_pred = sub_sec_list[i].split(" ")
            paper_secondary_field_sol = sol_sec_list[i].split(" ")

            diff = len(paper_secondary_field_pred)-len(paper_secondary_field_sol)

            if diff<0:
                tot = 0
                for sf_sol in paper_secondary_field_sol:
                    if sf_sol in paper_secondary_field_pred:
                        tot+=1
                tot /= len(paper_secondary_field_sol)
            else:
                tot = 0
                for sf_pred in paper_secondary_field_pred:
                    if sf_pred in paper_secondary_field_sol:
                        tot+=1

                tot /= len(paper_secondary_field_pred)

            secondary_field_acc += tot

        loss = secondary_field_acc/len(sol_sec_list) + primary_field_acc
        
        return loss

    except Exception as e:
        
        raise ParticipantVisibleError(f"Error occurred: {str(e)}")

In [67]:
score(pd_sol, pd_sol, "id")

2.0